In [1]:
import gym
import gym_codegen
import numpy as np
import dqn
from dqn import DQNAgent

import io
import os
import random
import sys


def main():
    print "Creating DQN agent..."

    iters = 10000
    n_goal = 0
    n_goal_all = 0
    time_stamp = 0

    ############################################################
    # print x
    # max_steps = 3
    # actions = ["print", " ", "x"]
    ############################################################

    ############################################################
    # print x+1
    max_steps = 5
    actions = ["print", " ", "x", "+", "1"]
    ############################################################

    ############################################################
    # for x in range(x):
    #  print x
    max_steps = 9
    actions = ["for", " ", "x", "in range(x):\n", "print"]
#     max_steps = 7
#     actions = ["for", " ", "x", "in range(x):\n", " print "]
    # max_steps = 15
    # actions = ["for", " ", "in", "range", "(", "x", ")", ":\n", "print"]
    ############################################################

    ############################################################
    # # for i in range(x,n):
    # #  print i
    # max_steps = 17
    # actions = ["for", " ", "i", "in", "range", "(", "x", ",", "n", ")", ":\n", "print"]
    ############################################################

    agent = DQNAgent(max_steps, actions)
    agent.dqn.initial_exploration = iters*0.8

    results = []
    policy_frozen = False
    wins_file = "wins.txt"
    with io.FileIO(wins_file, "w") as file:
        file.write("Winning codes:\n")

    for iter in range(iters):
        if iter % 10 == 0:
            print "\n::{}::".format(iter)

        if iter == 4300: # 2300:
            policy_frozen = True

        env = gym.make("codegen-v0")
        num = random.randrange(1,10) #(1,100)
        env.my_input = num

        ############################################################
        # print x
        # env.goal = str(num)
        ############################################################

        ############################################################
        # print x+1
        # env.goal = str(num + 1)
        ############################################################

        ############################################################
        # for x in range(x):
        #  print x
        env.goal = str("\n".join([str(i) for i in range(num)]))
        ############################################################

        code = env._reset()
        step_in_episode = 0
        total_score = 0.0
        reward = 0.0
        mystate = []
        my_state_new = []

        while step_in_episode < max_steps:
            state = env.code_index_list[:]
            state += np.zeros([max_steps - len(env.code_index_list), agent.dqn.code_idx_size], dtype=int).tolist()

            if step_in_episode == 0:
                action_idx = agent.start(code, state, policy_frozen)
            else:
                action_idx = agent.act(code, state, reward)

            code, reward, terminal, info = env._step(action_idx, agent.dqn.actions)
            state_prime = env.code_index_list[:]
            state_prime += np.zeros([max_steps - len(env.code_index_list), agent.dqn.code_idx_size], dtype=int).tolist()

            agent.dqn.experience_replay(agent.dqn.time_stamp)
            if step_in_episode == max_steps-1 or terminal:
                agent.dqn.stock_experience(agent.dqn.time_stamp, state, action_idx, reward, state_prime, True)
                if terminal:
                    agent.dqn.goal_idx.append(agent.dqn.time_stamp)
                agent.dqn.time_stamp += 1
            else:
                agent.dqn.stock_experience(agent.dqn.time_stamp, state, action_idx, reward, state_prime, False)

            total_score += reward

            if terminal:
                agent.end(reward)

                n_goal_all +=1
                step_in_episode += 1

                if iters-iter<=100:
                    n_goal +=1

            step_in_episode += 1

        if iter >= 100:
            results = results[1:]
        if reward >= 1:
            print "WIN"
            results.append(1.0)
            with io.FileIO(wins_file, "a") as f:
                f.write("\n=====================\n{}\n=====================\n\n".format(code))
                f.flush()
                os.fsync(f)
        else:
            results.append(0.0)
        total_iters = 100 if iter >= 100 else iter + 1
        
        if iter % 10 == 0:
            print "TOTAL {:.2f}% of wins in last {} iters, sum: {}, total good: {}".format(
                100 * sum(results) / total_iters, total_iters, sum(results), len(agent.dqn.goal_idx))

        if iter == 1 + agent.dqn.initial_exploration:
            print "n_goal_all = ", n_goal_all
            print agent.dqn.goal_idx
#             raw_input()
#         env._render()

    print "n_goal : ", n_goal
    print "epsilon : ", agent.epsilon

if __name__ == "__main__":
    main()

Creating DQN agent...
Prepare Data for pretraining...
good code!
good code!
good code!
good code!
good code!
good code!
good code!
good code!
good code!
good code!
good code!
good code!
good code!
good code!
good code!
good code!
good code!
good code!
good code!
good code!
good code!
good code!
good code!
good code!
number of Data start with 'for' : 24
number of Data start with ' ' : 0
number of Data start with 'x' : 0
number of Data start with 'in range(x):
' : 0
number of Data start with 'print' : 0

Data Size :  24
codebook: ['for', ' ', 'x', 'in range(x):\n', 'print']
Data index: 
for x in range(x):
 print x
for x in range(x):
 x  
for xforx in range(x):
 x
for xforx in range(x):
 print
for xfor  in range(x):
 x
for xprint in range(x):
 print 
for xprint in range(x):
 xprint
for xprint in range(x):
 x 
for xprint in range(x):
  x
for xprint  in range(x):
 print
for xprint  in range(x):
 x
for forfor  in range(x):
 x
for forfor  in range(x):
 print
for forfor in range(x):
 x 
for fo

[2017-01-19 15:31:40,638] Making new env: codegen-v0
[2017-01-19 15:31:40,808] Making new env: codegen-v0



::0::
Initializing Codegen Environment...
TOTAL 0.00% of wins in last 1 iters, sum: 0.0, total good: 0
Initializing Codegen Environment...
Code: 

import sys

x = int(sys.argv[1])

# desired code starts here
for xin range(x):
 x xx



[2017-01-19 15:31:40,840] Making new env: codegen-v0
[2017-01-19 15:31:40,867] Making new env: codegen-v0
[2017-01-19 15:31:40,904] Making new env: codegen-v0
[2017-01-19 15:31:40,944] Making new env: codegen-v0
[2017-01-19 15:31:40,962] Making new env: codegen-v0
[2017-01-19 15:31:40,980] Making new env: codegen-v0
[2017-01-19 15:31:41,018] Making new env: codegen-v0
[2017-01-19 15:31:41,036] Making new env: codegen-v0


Initializing Codegen Environment...
Code: 

import sys

x = int(sys.argv[1])

# desired code starts here
 x in range(x):
 x in range(x):
 

Initializing Codegen Environment...
Code: 

import sys

x = int(sys.argv[1])

# desired code starts here
printprintprint xprintprint in range(x):


Initializing Codegen Environment...
Code: 

import sys

x = int(sys.argv[1])

# desired code starts here
 print xprint in range(x):
forx

Initializing Codegen Environment...
Code: 

import sys

x = int(sys.argv[1])

# desired code starts here
 for xprintxin range(x):
printprint

Initializing Codegen Environment...
Code: 

import sys

x = int(sys.argv[1])

# desired code starts here
for xxprint   in range(x):


Initializing Codegen Environment...
Code: 

import sys

x = int(sys.argv[1])

# desired code starts here
in range(x):
in range(x):
for  print in range(x):
 

Initializing Codegen Environment...
Code: 

import sys

x = int(sys.argv[1])

# desired code starts here
printin range(x):
for xforfor print

...

Initializing Codegen Environment...
Code: 

import sys

x = int(sys.argv[1])

# desired code starts here
in range(x):
xprint x x print



[2017-01-19 15:57:38,093] Making new env: codegen-v0


Initializing Codegen Environment...
Code: 

import sys

x = int(sys.argv[1])

# desired code starts here
forin range(x):
forprint forfor  



[2017-01-19 15:57:38,674] Making new env: codegen-v0


Initializing Codegen Environment...
Code: 

import sys

x = int(sys.argv[1])

# desired code starts here
xxprintprint xx for

n_goal :  0
epsilon :  1.0
Code: 

import sys

x = int(sys.argv[1])

# desired code starts here
xforxforx printxprint

